# pH-dependence on added contaminants in water

<p class="acknowledgement">Written by Svetlana Kyas (ETH Zurich) on Mar 31th, 2022</p>

```{attention}
Always make sure you are using the [latest version of Reaktoro](https://anaconda.org/conda-forge/reaktoro). Otherwise, some new features documented on this website will not work on your machine and you may receive unintuitive errors. Follow these [update instructions](updating_reaktoro_via_conda) to get the latest version of Reaktoro!
```

This tutorial shows how to model the dependence of pH on various contaminants in the water (which affect both fish life and the general ecosystem) in Reaktoro.

In the image below, we see the green scum that represents the worst algal bloom Lake Erie (North America) has seen in decades. The photo was taken in October 2011 from the orbit of the Landsat-5 satellite. This happened due to record-breaking torrential rains in the spring that washed fertilizer into the lake and spurred the growth of the microcystin-producing cyanobacteria bloom.

|![Toxic algae bloom in lake Erie](../../images/applications/toxic-algae-bloom-lake-erie.jpeg)|
|:--:|
|Toxic algae bloom in the Lake Erie, Source: NASA Earth Observatory|

First, the chemical system is set up with a single aqueous phase (governed by the HKF activity model) and the chemical state corresponding to pure water (with pH = 7) is initialized.

In [1]:
from reaktoro import *
import pandas as pd

# Define the thermodynamic database
db =  SupcrtDatabase("supcrt98")

# Define the aqueous phase
aqueousphase = AqueousPhase(speciate("H O Na Cl N"))
aqueousphase.set(ActivityModelHKF())
# Define the chemical system:
system = ChemicalSystem(db, aqueousphase)

# Define the chemical state corresponding to the pure water
state = ChemicalState(system)
state.setTemperature(25, "celsius")
state.setPressure(1.0, "bar")
state.set("H2O(aq)", 1.0, "kg")

# Define the equilibrium solver and solve the equilibrium problem with the initial chemical state
solver = EquilibriumSolver(system)
solver.solve(state)

# Define aqueous properties of the chemical state
aprops = AqueousProps(state)
print("pH of pure water = ", aprops.pH())

pH of pure water =  6.99756


## Adding acidic contaminant or decreasing pH

First, we study the behavior of the pH when the acidic contaminant is added to the water. We define the auxiliary lists with the amounts of the acid HCl in the chemical state `hcl_amounts`. In the 50 steps, we gradually add 0.1 mmol of hydrogen chloride and evaluate the pH in the obtained state, which is collected in the `pandas.DataFrame`.

In [2]:
# Initialize lists with HCl amounts and ph values
hcl_0 = 0.0
hcl_delta = lambda i: 0.01 if i < 10 else 0.1
nsteps = 60

# Define dataframe and initialize it with the first values oof HCl and pH
pd1 = pd.DataFrame(columns=["amount_HCl", "pH"])
pd1.loc[len(pd1)] = [hcl_0, aprops.pH().val()]

for i in range(nsteps):

    # Add an increment of hydrogen chlorite to the state
    state.add("HCl(aq)", hcl_delta(i), "mmol")

    # Equilibrate state with updated problem
    solver.solve(state)

    # Update aqueous properties
    aprops.update(state)

    # Update amount of HCl
    hcl_0 += hcl_delta(i)

    # Append new calculated value to the dataframe
    pd1.loc[len(pd1)] = [hcl_0, aprops.pH().val()]

### Adding ammonia or increasing pH

The addition of a chemical contaminant such as ammonia (a compound of nitrogen and hydrogen with the formula NH3, a colorless gas with a characteristic pungent odour) can increase pH and affect fish life.

In [3]:
state = ChemicalState(system)
state.setTemperature(25, "celsius")
state.setPressure(1, "bar")
state.set("H2O(aq)", 1.0, "kg")
solver.solve(state)
aprops.update(state)

nh3_0 = 0.0
nh3_delta = lambda i: 0.01 if i < 10 else 0.1
nsteps = 60

pd2 = pd.DataFrame(columns=["amount_NH3", "pH"])

pd2.loc[len(pd1)] = [nh3_0, aprops.pH().val()]

for i in range(nsteps):

    # Add an increment of ammonia to the chemical state
    state.add("NH3(aq)", nh3_delta(i), "mmol")

    # Equilibrate state with updated problem
    solver.solve(state)

    # Update aqueous properties
    aprops.update(state)

    # Update the amount of NH3
    nh3_0 += nh3_delta(i)

    # Append new calculated value to the dataframe
    pd2.loc[len(pd2)] = [nh3_0, aprops.pH().val()]

### Plotting the pH dependencies

We plot pH as a function of the added amounts of HCl and NH<sub>3</sub>.

In [6]:
from reaktplot import * 

fig = Figure()
fig.title("pH DEPENDENCE ON HCL AMOUNT")
fig.xaxisTitle('HCl [mol]')
fig.yaxisTitle('pH')
fig.drawLineWithMarkers(pd1["amount_HCl"], pd1["pH"], "pH")

fig.show()

In [8]:
from reaktplot import * 

fig = Figure()
fig.title("pH DEPENDENCE ON NH3 AMOUNT")
fig.xaxisTitle('NH3 [mol]')
fig.yaxisTitle('pH')
fig.drawLineWithMarkers(pd2["amount_NH3"], pd2["pH"], "pH")

fig.show()

As expected, adding a contaminant like HCl into water increases free H<sup>+</sup> ions and decreases pH according to the reaction

$$
\rm{HCl(aq) + H_2O(l) = H_3O^+ + Cl^-},
$$

affecting the ecosystem. Whereas adding ammonia removes H<sup>+</sup> from water to produce ammonium and hydroxide, i.e., to produce ammonium and hydroxide:

$$
\rm{NH_3 + H_2O = NH_4^+ + OH^-}.
$$